In [1]:
import matplotlib.pyplot as plt
import numpy as np
import math as mt
import seaborn as sns
from tqdm import tqdm
import pandas as pd
from hangul_utils import split_syllables, join_jamos
from tqdm.auto import tqdm
import re
from konlpy.tag import Mecab
#from eunjeon import Mecab
from hanspell import spell_checker

In [2]:
con_dict = [
    
    ['ㅏㅣ','ㅐ'], ['ㅑㅣ','ㅒ'], ['ㅓㅣ','ㅔ'],
    ['ㅕㅣ','ㅖ'], ['ㅗㅣ','ㅚ'], ['ㅗㅐ','ㅙ'],
    ['ㅜㅓ','ㅝ'], ['ㅜㅔ','ㅞ'], ['ㅡㅣ','ㅢ'],
    ['ㅣㅏ','ㅑ'], ['ㅣㅓ','ㅕ'], ['ㅣㅗ','ㅛ'],
    ['ㅣㅜ','ㅠ'], ['ㅡㅓ','ㅓ'], ['ㅗㅏ','ㅘ']
    
]

jongsung_list = [ 'ㄱ', 'ㄲ', 'ㄳ', 'ㄴ', 'ㄵ', 'ㄶ', 'ㄷ', 'ㄹ', 'ㄺ', 'ㄻ', 'ㄼ', 'ㄽ', 'ㄾ', 'ㄿ', 'ㅀ', 'ㅁ', 'ㅂ', 'ㅄ', 'ㅅ', 'ㅆ', 'ㅇ', 'ㅈ', 'ㅊ', 'ㅋ', 'ㅌ', 'ㅍ', 'ㅎ']


#lis_beta = ['EP+EF', 'VCP+EF', 'B+EF', 'B+EP+EF', 'B+VCP+EF', 'EF','EP']

lis_beta = ['EP+EF', 'EF', 'B+EF', 'B+EP+EF']

#어말을 처리해 주기 위한 것으로, 나중에 EC등이 필요해 진다면 이 부분에 EC 등을 집어넣어준다. 참고로 말하자면 이는 마지막에 위치해야한다.
#특이 바로 밑의 이 부분은 형태소 태그가 이 리스트 안의 것과 일치하는 경우 단순 삭제를 하는 것이고
lis_beta_ef = ['EP+EP+EF', 'EP+EF', 'EF', 'UNKNOWN']

lis_beta_ef_h = ['EF', 'UNKNOWN']

#이 부분 같은 경우는 마지막에 오는 것을 처리하는 것으로 단독으로만 들어가는게 좋겠지?
lis_tag_last = ['EF', 'UNKNOWN']

lis_end = [
    
    'ㅂㄴㅣㄷㅏ', 'ㅂㅅㅣㄷㅏ', 'ㅅㅣㄷㅏ', 
    'ㅅㅔㅇㅛ', 'ㄷㅔㅇㅛ', 'ㅇㅔㅇㅛ', 'ㅇㅖㅇㅛ', 'ㄴㅏㅇㅛ', 'ㅇㅡㄹㄲㅏㅇㅛ', 'ㅇㅣㄹㄲㅏㅇㅛ', 'ㄹㄲㅏㅇㅛ', 'ㅇㅡㄴㄱㅏㅇㅛ', 'ㅇㅣㄴㄱㅏㅇㅛ','ㅇㅛ',
    'ㅈㅛ',
    'ㅅㅣㅂㅅㅣㅇㅗ', 'ㅅㅣㅇㅗ', 'ㅇㅗ',
    'ㅂㄴㅣㄲㅏ', 'ㅅㅡㅂㄴㅣㄷㅏ',  
    
]

lis_end_2low = [
    
    'ㄷㅓㄹㅏ','ㄴㄷㅏ', 'ㅆㄷㅏ', 'ㄹㅗㄷㅏ', 'ㄷㅏ', 'ㄱㅔ', 'ㅈㅣ', 'ㅈㅏ', 
    'ㄹㅏ',
    'ㅇㅑ', 
    'ㄴㅣㄲㅏ', 
    'ㄲㅏ', 
    'ㄴㅣ', 
    'ㅇㅏ', 
    'ㄷㅔ', 
    
]

# lis_end_2low = [
    
#     'ㄷㅓㄹㅏ','ㄴㄷㅏ', 'ㅆㄷㅏ', 'ㄷㅏ', 
#     'ㄹㅏ',
#     'ㅇㅑ', 
    
# ]

P_LIST = ['.', '?', '!', '\'', '\"', 'ᆞ', 'ᆢ', 'ㆍ',  '”', '’',')', '(', ',']

SV_LIST = ['\'', '\"', ':', ';']

lis_plus = [
    
    'EP', 'VCP', 
    
]

In [3]:
mec = Mecab()

In [4]:
def detect_h(input, lis_end_h, lis_end_l):
    for i in lis_end_h:
        if len(input)>=len(i):
            if input[-len(i):]==i:
                return 1
            
    for i in lis_end_l:
        if len(input)>=len(i):
            if input[-len(i):]==i:
                return 0
            
    return -1

def unite(input, dict):
    for i in dict:
        input = re.sub(i[0],i[1],input)
    return input
    
## 자모 단위로 문장을 나누고 합칠 때 쓰는 class ##
class Jamodealer:
    jamo = []
    pp = ''
    #각 단어들을 받아와서 자모단위로 나눈다.
    def __init__(self,lis_word):
    
        self.jamo = []
        for i in lis_word:
            self.jamo.append(split_syllables(i))
    
    ##사전에서 변환된 자모단위로 분리된 문장을 합칠 때 쓰는 함수이다.     
    def make_one(self):
        #list 형태로 저장된 자모들의 집합을 하나의 string pp에 저장한다. 
        self.pp = ''
        for i in self.jamo:
             self.pp= self.pp+i
        ##종성과 종성을 합쳐야 하는 경우가 있다면 합친다.        
        self.pp = unite(self.pp, con_dict)
        
        #자모 단위의 string에서 자모 단위로 사전을 만들고 거기에 index를 부여한다.        
        chars = list(set(self.pp))
        char_to_ix = { ch:i for i,ch in enumerate(chars) }
        ix_to_char = { i:ch for i,ch in enumerate(chars) }
        
        #자모 단위로 분리되었던 문장을 다시 하나로 합친다.
        jamo_numbers = [char_to_ix[x] for x in self.pp]
        restored_jamo = ''.join([ix_to_char[x] for x in jamo_numbers])
        #합쳐진 문장을 return 한다.
        restored_text = join_jamos(restored_jamo)
        return restored_text

def to2lists(input):
    lis_word = []
    lis_tag = []
    #data = han.pos(input,ntags=22,flatten=True, join=False)
    data = mec.pos(input)
    for i in data:
        lis_word.append(i[0])
        lis_tag.append(i[1])
    return lis_word, lis_tag

def rememberSpace(lis, input):
    
    rlis = []
    
    for i in range(len(lis)):
        if lis[i]==input:
            rlis.append(i)
            
    for i in range(len(rlis)):
        rlis[i] = rlis[i]-i      
    return rlis

def convertSpace(lis_space,lis_lis):
    
    rlis = []
    k=0
    for i in range(len(lis_lis)):
        
        if k in lis_space:
            rlis.append(i)
            
        k = k+len(lis_lis[i])
        
    #print(rlis)  
    return rlis

def union(lis, lis_lis):
    
    k = 0
    for i in lis:
        lis_lis.insert(i+k,' ')
        k = k+1

def union_t_03(lis_tag):
    
    for i in range(1, len(lis_tag)):
        if lis_tag[i-1] ==' ' or lis_tag[i]==' ':
            lis_tag[i] = lis_tag[i]
        else:
            lis_tag[i] = '/'+lis_tag[i]
            
def union_w_03(lis_w, lis_tag):
    
    for i in range(1, len(lis_w)):
        if lis_tag[i]==' SF':
            lis_w[i] = ' '+lis_w[i+1]

In [5]:
def prepro(input):
    lis_w, lis_t = to2lists(input)  
    
    
    space_list = rememberSpace(input,' ')
    space_location = convertSpace(space_list, lis_w)
    

    
    union(space_location, lis_w)
    union(space_location, lis_t)
    

    
    union_t_03(lis_t)
    union_w_03(lis_w, lis_t)
    

    str_w = ''
    str_t = ''
    for i in range(len(lis_w)):
        str_w = str_w + lis_w[i]
        str_t = str_t + lis_t[i]
    
    
    data_w = str_w.split(' ')
    data_t = str_t.split(' ')
    
    lis_word, lis_tag = to2lists(input)
    
    lis_ind = []
    t_ind = 0
    jam1 = Jamodealer(lis_word)
    jam2 = Jamodealer(data_w)
    for i in range(len(data_w)):
        element = []
        leng = len(data_t[i].split('/'))
        res = jam2.jamo[i]
        ind = 0
        lenlen = 0
        #element.append(0)
        for j in range(leng):
            element.append(ind)
            ind = ind + len(jam1.jamo[t_ind])
            res = res[len(jam1.jamo[t_ind]):]
            
            lenlen = len(jam1.jamo[t_ind])+lenlen
            t_ind = t_ind+1

        element.append(len(jam2.jamo[i]))
        lis_ind.append(element)
        
    return data_w, data_t, lis_ind

In [6]:
def prepro_a(input):
    lis_w, lis_t = to2lists(input)  
    

    
    space_list = rememberSpace(input,' ')
    space_location = convertSpace(space_list, lis_w)
    
    
    
    union(space_location, lis_w)
    union(space_location, lis_t)
    

    
    union_t_03(lis_t)
    union_w_03(lis_w, lis_t)
    

    str_w = ''
    str_t = ''
    for i in range(len(lis_w)):
        str_w = str_w + lis_w[i]
        str_t = str_t + lis_t[i]
    
    
    data_w = str_w.split(' ')
    data_t = str_t.split(' ')
    
    lis_word, lis_tag = to2lists(input)
    
    lis_ind = []
    t_ind = 0
    jam1 = Jamodealer(lis_word)
    jam2 = Jamodealer(data_w)
    for i in range(len(data_w)):
        element = []
        leng = len(data_t[i].split('/'))
        res = jam2.jamo[i]
        ind = 0
        lenlen = 0
        #element.append(0)
        for j in range(leng):
            element.append(ind)
            ind = ind + len(jam1.jamo[t_ind])
            res = res[len(jam1.jamo[t_ind]):]
            
            lenlen = len(jam1.jamo[t_ind])+lenlen
            t_ind = t_ind+1

        element.append(len(jam2.jamo[i]))
        lis_ind.append(element)
        
    return data_w, data_t, lis_ind

In [7]:
def prepro_beta_05(input, lis_ef, tag_last, lis_w_last, lis_w_last_not):
    data_w, data_t, lis_ind = prepro(input)
    
    last_words = []

    data_w_jamo = []

    data_t_after = []
    
    lis_target_ind = []
    
    for i in data_w:
        jam_ele = Jamodealer(i)
        ele = ''
        for j in jam_ele.jamo:
            ele = ele+j
        data_w_jamo.append(ele)
    
    for i in range(len(data_t)):
        #if i<len(data_t)-1:
        if i<len(data_t):
            lis_res = []
            for ind in range(len(lis_ind[i])-1):
                lis_res.append(data_w_jamo[i][lis_ind[i][ind]:lis_ind[i][ind+1]])

        
        if 'EF/SF' in data_t[i] or 'EF/SV' in data_t[i] or 'UNKNOWN/SF' in data_t[i] or 'UNKNOWN/SV' in data_t[i]:# and 'EC/SF' not in data_t[i]:
            if 'EF/SF' in data_t[i] or 'UNKNOWN' in data_t[i]:
                elements = data_t[i].split('/')
                flag = 0
                
                for j in range(len(elements)):
                
                    flag_end = detect_h(lis_res[j], lis_w_last_not, lis_w_last)
                    if elements[j] in lis_ef and flag_end==0: #and j == len(elements)-1:
                        elements[j] = 'NULL'
                    
                        last_words.append(data_w_jamo[i][lis_ind[i][j]:lis_ind[i][j+1]])
                        lis_res[j]=''
                    
                        lis_target_ind.append(i)
                    
#                         elements_post = '/'.join(elements)
#                         data_t_after.append(elements_post)
                        
                    elif 'EF' in elements[j] and flag_end==0:# + EF를 처리하는 부분이므로 + EF 만을 마지막에서 처리한다.
#                         print('wwww')
                        for jam in lis_w_last:
                            if len(lis_res[j])>=len(jam):
                                
                                res_out_punc = lis_res[:lis_ind[i][-2]][j]

                                if res_out_punc[-len(jam):]==jam:
                                
                                    lis_target_ind.append(i)
                                
                                    last_words.append(jam)
                                    lis_res[j] = lis_res[j].replace(jam, '', 1)

                                    for k in tag_last:

                                        if k in elements[j]:
                                        
                                            if '+' in elements[j]:
                                            
                                                ind = elements[j].index('+'+k)
                                                elements[j] = elements[j][:ind]
                                    break
                                
                                elif lis_w_last.index(jam)==len(lis_w_last)-1:#new
                                    for k in tag_last:

                                        if k in elements[j]:
                                        
                                            if '+' in elements[j]:
                                            
                                                ind = elements[j].index('+'+k)
                                                elements[j] = elements[j][:ind]
                                            
                                    lis_target_ind.append(i)
                                    last_words.append('')
                                    break

                
                elements_post = '/'.join(elements)
                data_t_after.append(elements_post)
                
                data_w_jamo[i] = ''.join(lis_res)

                #elements_post = '/'.join(elements)
                #data_t_after.append(elements_post)
                    
            #######################################
            
            #data_t_after.append(data_t[i])
            
        elif 'EC/SF' in data_t[i]:
#             print('ee')
            elements = data_t[i].split('/')
            
            flag = 0
            for j in range(len(elements)):
                
                flag_end = -1
                if elements[j]=='EC':
                    flag_end = detect_h(lis_res[j], lis_w_last_not, lis_w_last)
                        
#                 print(elements[j])
#                 print(flag_end)
                if flag_end==0 and i not in lis_target_ind:
                    lis_target_ind.append(i)
                    last_words.append('')
#             print(data_t[i])
            data_t_after.append(data_t[i])
            
        else:
            data_t_after.append(data_t[i])
            
        
        #################################################################
        
        
        lis_normal = []
    
        for i in data_w_jamo:
            jam_n = Jamodealer(i)
            lis_normal.append(jam_n.make_one())
    
#         lis_target_ind = []

#         word_test_pre, tag_test_pre, ind_test_pre = prepro(input)
    
    
#         for i in range(len(lis_normal)):
#             if lis_normal[i]!=data_w[i]:
#                 lis_target_ind.append(i)
        
        
        
        
        
    return data_w, data_t, lis_ind, data_w_jamo, data_t_after, last_words, lis_target_ind
                        
    

In [8]:
def convert_not(stc, tag, ex):
    ind_point = -1
    point = ''

#     for i in P_LIST:
#         if stc.find(i) !=-1:
#             point = i
#             break
            
    for i in range(len(stc)):
        if stc[i] in P_LIST:
            point = stc[i]
            break
            
    if point in P_LIST:
        ind_point = stc.index(point)
    
    r_word = ''
    r_pun = ''
    
    if ind_point!=-1:
        r_word = stc[:ind_point]
        r_pun = stc[ind_point:]
    else:
        r_word = stc
        
    return r_word + ex + r_pun

def convert_an(stc, tag, ex):
    
    ind_point = -1
    point = ''

#     for i in P_LIST:
#         if stc.find(i) !=-1:
#             point = i
#             break
            
    for i in range(len(stc)):
        if stc[len(stc) - i] in P_LIST:
            point = stc[len(stc) - i]
            break
            
    if point in P_LIST:
        ind_point = stc.index(point)
    
    r_word = ''
    r_pun = ''
    
    if ind_point!=-1:
        r_word = stc[:ind_point]
        r_pun = stc[ind_point:]
    else:
        r_word = stc
    
    if ex=='ㄹㅏ':
        
        if len(r_word)!=0:
            if 'ㅗ'==stc[-2]:
                return r_word+'ㅏㅇㅛ'+r_pun
            elif 'ㅎㅏ'==stc[-3:-1]:
                return r_word+'ㅣㅇㅛ'+r_pun
            elif 'ㄷㅏㄹ' in stc:
                return r_word+'ㄹㅏ'+r_pun
                if 'VA' not in tag:
                    return r_word+'ㄹㅏㅇㅛ'+r_pun
                return r_word[:-3]+'ㅈㅜㅅㅔㅇㅛ'+r_pun
            elif 'ㅗㄹ' == r_word[-2:]:
                return r_word+'ㄹㅏㅇㅛ'+r_pun
            else:

                return r_word+'ㅇㅛ'+r_pun
        else:
            return r_word+ex+r_pun

        #return r_word+'ㅇㅛ'+r_pun
    elif ex=='ㄱㅜㄴㅏ':
        return r_word+'ㄱㅜㄴㅇㅛ'+r_pun
    elif ex=='ㅈㅏㄶㄴㅣ':
        return r_word+'ㅈㅏㄶㅇㅏㅇㅛ'+r_pun
    elif ex=='ㄱㅔ':###############################
        print(r_word)
        if 2<=len(r_word) and r_word[-2:]=='ㅎㅏ':
            return r_word+'ㅣㅇㅛ'+r_pun
        elif 2<=len(r_word) and r_word[-2:]=='ㅅㅣ':
            return r_word+'ㅓㅇㅛ'+r_pun
        return r_word+'ㄱㅔㅇㅛ'+r_pun
        
    elif ex=='ㅇㅓㄹㅏ':
        return r_word+'ㅇㅓㅇㅛ'+r_pun
    elif ex=='ㅇㅏㄹㅏ':
        return r_word+'ㅇㅏㅇㅛ'+r_pun
    elif ex=='ㄴㅗㄹㅏ':
        if stc[-3:-1]=='ㅎㅏ':
            return r_word+'ㅣㅇㅛ'+r_pun
        else:
            return r_word+'ㅇㅓㅇㅛ'+r_pun
    elif ex=='ㄷㅏㄷㅓㄹㅏ':
        return r_word+'ㄷㅐㅇㅛ'+r_pun
    elif ex=='ㄷㅓㄹㅏ':
        wd = ''
        if 'ㄷㅏ' in r_word:
#             print('dd')
            return r_word[:-1]+'ㅐㅇㅛ'+r_pun
        if r_word[-1] in jongsung_list:
            wd = r_word[-2]
        else:
            wd = r_word[-1]
        if wd=='ㅗ':
            return r_word+'ㅏㅇㅛ'+r_pun
        elif wd=='ㅜ':
            return r_word+'ㅓㅇㅛ'+r_pun
        elif wd=='ㅏ':
            return r_word+'ㅇㅏㅇㅛ'+r_pun
        else:
            return r_word+'ㅇㅓㅇㅛ'+r_pun
    elif ex=='ㄴㅣ' or ex =='ㄴㅡㄴㄱㅏ' or ex =='ㅇㅡㄴㄱㅏ':
        
        isVcp = tag[-11:-3]
        
        if isVcp =='VCP' or isVcp =='/VCP' or isVcp =='NNG/VCP':
            return r_word + 'ㅇㅖㅇㅛ' + r_pun
        elif isVcp == 'VCP/NULL':
            return r_word + 'ㅇㅔㅇㅛ' + r_pun
        
        
        if ex=='ㄴㅣ' and stc[-3:-1]=='ㅌㅔ':
            return r_word+'ㄴㅣㅇㅛ'+r_pun
        
        if ex=='ㄴㅣ' and 'NNG' in tag:
            return r_word+'ㅇㅖㅇㅛ'+r_pun
        
        return r_word+'ㄴㅏㅇㅛ'+r_pun
    elif ex=='ㅇㅑ':
        return r_word+'ㅇㅔㅇㅛ'+r_pun
#     elif ex=='ㄷㅓㄹㅏ':
#         if 'ㄷㅏ' in stc:
#             return stc[:-1]+'ㅔㅇㅛ'
#         return stc+'ㄷㅔㅇㅛ'
    elif ex=='ㅈㅣ':
        return r_word+'ㅈㅛ'+r_pun
    elif ex=='ㅈㅏ':
        return r_word+'ㅈㅛ'+r_pun
    else:
        return r_word+ex+'ㅇㅛ'+r_pun
    
def convert_da(stc, tag, ex):
    #print(tag)
    if 'UNKNOWN/' in tag:
        isVcp = tag[-14:]
    else:
        isVcp = tag[-6:]

    isETM = tag[-12:]


    ind_point = -1
    point = ''

    for i in range(len(stc)):
        if len(stc)-i-1==0:
            point = stc[0]
            ind_pont = -1
        if stc[len(stc) - i-1] not in P_LIST:
            point = stc[len(stc) - i-1]
            ind_point = len(stc)-i

            break
    
#     print(ind_point)
    
#     if point in P_LIST:
#         ind_point = stc.index(point)
    
    r_word = ''
    r_pun = ''

    if ind_point!=-1:
        r_word = stc[:ind_point]
        r_pun = stc[ind_point:]
    else:
        r_word = ''
        r_pun = stc[0]
    
    try:
        jongsung = r_word[-1]
    
    except:
        return ex+r_pun
        
    if jongsung in jongsung_list:
        if  isETM.find('+ETM') != -1:
            r_word = r_word[:-1]
            final = r_word +'ㅂㄴㅣㄷㅏ'+r_pun
        else:
            final = r_word +'ㅅㅡㅂㄴㅣㄷㅏ'+r_pun
    else:
        if isVcp.find('VCP') != -1:
            if len(r_word)>=2:
                if 'ㅇㅣ' in r_word:
                    return r_word +'ㅂㄴㅣㄷㅏ'+r_pun
            final = r_word +'ㅇㅣㅂㄴㅣㄷㅏ'+r_pun
        elif 'SN/NULL' in tag:
            final = r_word +'ㅇㅣㅂㄴㅣㄷㅏ'+r_pun
        else:
            final = r_word +'ㅂㄴㅣㄷㅏ'+r_pun
    #print(final)
    return final

In [9]:
class Changer(object):
    
    def make_end_h(self, stc, tag, ex):

#         print(ex)
        if 'ㄷㅏ'== ex[-2:]:

            return convert_da(stc, tag, ex)
            #return convert_not(stc, tag, ex)
        else:
            return convert_not(stc, tag, ex)
            #return convert_an(stc, tag, ex)

    
    def to_high(self, input):
        
        if '  ' in input:
            return input
        
        result = input
        space_list = rememberSpace(input,' ')
        
        test_w, test_t = to2lists(result)
        pre_w, pre_t, pre_ind = prepro(result)
        
        data_w, data_t, lis_i, lis_w, lis_t, off_word, lis_target_ind = prepro_beta_05(result, lis_beta_ef, lis_tag_last, lis_end_2low, lis_end)
        
#         lis_w, lis_t, lis_i, w_last, t_last, off_word, lis_normal, lis_target_ind = prepro_after(result, lis_end_2low)
#         space_location = convertSpace(space_list, pre_w)
        space_location = convertSpace(space_list, data_w)
#         lis_target_final = []
        
        if len(lis_target_ind)!=0:

            jam = Jamodealer(data_w)

            for i in range(len(lis_target_ind)):
#                 print(lis_target_ind)
#                 print(i)
#                 print(lis_w[10])
#                 print(lis_t[10])
#                 print(off_word)
#                 print(lis_target_ind[0])
                new_end = self.make_end_h(lis_w[lis_target_ind[i]], lis_t[lis_target_ind[i]], off_word[i])
                jam.jamo[lis_target_ind[i]] = new_end
            
            
#             jam.jamo.append(w_last)
            union(space_location, jam.jamo)
            return jam.make_one()

        return input


    
        
    def processText(self,stc):
        result = stc
        
        flag = 0
        if result[-1]=='\n':
            result = result.replace('\n','')
        
        num = 0
        while 1:
            if result[-1-num]!=' ':
                break
            else:
                num = num+1
                
        
                
        if num==0:
            rere = result
        else:
            rere = result[:-num]
            
        
        r_pun = ''
        r_word = rere
        while True:
            if r_word[-1] in SV_LIST:
                r_pun = r_pun+r_word[-1]
                r_word = r_word[:-1]
            else:
                break
        
        
        num_space = 0
        for i in r_word:
            if i==' ':
                num_space = num_space+1
            else:
                break
            
        if num_space!=0:
            r_word = r_word[num_space:]

#         cc = ch.processText(line)
    
        plus = ''
        for s in range(num_space):
            plus = plus+' '
    
        if r_word[-1] =='?' or r_word[-1] =='.' or r_word[-1] =='!' or r_word[-1] =='\"':
            r_word = r_word
        else:
            r_word = r_word+'.'
            flag = 1
        try:
            res = self.to_high(r_word)
        except:
            res = r_word
            
        r_word = plus+r_word
        res = plus+res
        
        
        
#         if r_word[-1] =='?' or r_word[-1] =='.' or r_word[-1] =='!' or r_word[-1] =='\"':
#             r_word = r_word
#         else:
#             r_word = r_word+'.'
#             flag = 1
        
#         res = self.to_high(r_word)
        
        if flag ==1:
            res = res[:-1]
        
        #spacing = Spacing()
        #res = spacing(res)
        return res+r_pun[::-1]

In [10]:
print(prepro_beta_05('「지방세특례제한법」제92조의2제1항 각 호의 구분에 따른 세액공제금액은 다음과 같다.1. 자동계좌이체 방식에 의한 납부만을 신청한 경우 : 고지서 1장당 150원.', lis_beta_ef, lis_tag_last, lis_end_2low, lis_end))

(['「지방세특례제한법」제92조의2제1항', '각', '호의', '구분에', '따른', '세액공제금액은', '다음과', '같다.1.', '자동계좌이체', '방식에', '의한', '납부만을', '신청한', '경우', ':', '고지서', '1장당', '150원.'], ['SSO/NNG/NNG/XSN/NNG/SSC/XPN/SN/NNG/JKG/SN/XPN/SN/NNG', 'MM', 'NNG', 'NNG/JKB', 'VV+ETM', 'NNG/NNG/NNG/JX', 'NNG/JKB', 'VA/EC/SY/SN/SF', 'NNG/NNG/NNG', 'NNG/JKB', 'VV+ETM', 'NNG/JX/JKO', 'NNG/XSA+ETM', 'NNG', 'SC', 'NNG', 'SN/NNBC/XSN', 'SN/NNBC/SF'], [[0, 1, 8, 13, 15, 21, 22, 24, 26, 28, 30, 31, 33, 34, 37], [0, 3], [0, 4], [0, 5, 7], [0, 5], [0, 5, 10, 16, 19], [0, 5, 7], [0, 3, 5, 6, 7, 8], [0, 5, 9, 13], [0, 6, 8], [0, 5], [0, 5, 8, 11], [0, 6, 9], [0, 5], [0, 1], [0, 6], [0, 1, 4, 7], [0, 3, 6, 7]], ['「ㅈㅣㅂㅏㅇㅅㅔㅌㅡㄱㄹㅖㅈㅔㅎㅏㄴㅂㅓㅂ」ㅈㅔ92ㅈㅗㅇㅢ2ㅈㅔ1ㅎㅏㅇ', 'ㄱㅏㄱ', 'ㅎㅗㅇㅢ', 'ㄱㅜㅂㅜㄴㅇㅔ', 'ㄸㅏㄹㅡㄴ', 'ㅅㅔㅇㅐㄱㄱㅗㅇㅈㅔㄱㅡㅁㅇㅐㄱㅇㅡㄴ', 'ㄷㅏㅇㅡㅁㄱㅘ', 'ㄱㅏㅌㄷㅏ.1.', 'ㅈㅏㄷㅗㅇㄱㅖㅈㅘㅇㅣㅊㅔ', 'ㅂㅏㅇㅅㅣㄱㅇㅔ', 'ㅇㅢㅎㅏㄴ', 'ㄴㅏㅂㅂㅜㅁㅏㄴㅇㅡㄹ', 'ㅅㅣㄴㅊㅓㅇㅎㅏㄴ', 'ㄱㅕㅇㅇㅜ', ':', 'ㄱㅗㅈㅣㅅㅓ', '1ㅈㅏㅇㄷㅏㅇ', '150ㅇㅝㄴ.'], ['SSO/NNG/NNG/XSN/NNG/SSC/XPN/SN/NNG/JKG/SN/XPN/SN/NNG', 'MM', 'NNG', 'NNG/JKB', 'VV+ETM', 'NNG/NNG/NNG

In [11]:
ch = Changer()
ch.to_high('“변한의 나라에서는 철이 생산되는데 한·예·왜인들이 모두 와서 사간다.”, “왜와 가까운 지역이므로 남녀가 문신을 하기도 한다.”라는 중국의 역사서 『삼국지』의 기록을 통하여 엿볼 수 있다.')

'“변한의 나라에서는 철이 생산되는데 한·예·왜인들이 모두 와서 사갑니다.”, “왜와 가까운 지역이므로 남녀가 문신을 하기도 하.”라늡니다 중국의 역사서 『삼국지』의 기록을 통하여 엿볼 수 있습니다.'

In [12]:
kr = open('./aihub.mecab.shuf', "r" , encoding = "utf-8")
origin = open('./아카이브/aihub.kr.shuf', "r" , encoding = "utf-8")


부호 = ['.', '?', '!', ')', '"', '…', '”', '．', ':', '~', ']', '┃', ',', '」']

요 = 0
다 = 0
까 = 0
나머지 = 0
count = 0

result=kr.readline()
ori = origin.readline()


    
while True:

    
    
    result = result.replace('\n','')
    ori = ori.replace('\n','')
    if not result: break
    
    if 'ㅂ니다' in result:
        count = count+1
        print(result)
        print(ori)
        print(count)
        
        
    result=kr.readline()
    ori = origin.readline()

kr.close()

FileNotFoundError: [Errno 2] No such file or directory: './aihub.mecab.shuf'

In [ ]:
number_01

In [13]:
kr = open('./aihub.mecab.shuf_01', "r" , encoding = "utf-8")
origin = open('./아카이브/aihub.kr.shuf', "r" , encoding = "utf-8")


부호 = ['.', '?', '!', ')', '"', '…', '”', '．', ':', '~', ']', '┃', ',', '」']

요 = 0
다 = 0
까 = 0
나머지 = 0
count = 0

result=kr.readline()
ori = origin.readline()


    
while True:

    
    
    result = result.replace('\n','')
    ori = ori.replace('\n','')
    if not result: break
    
    if 'ㅂ니다' in result:
        count = count+1
        print(result)
        print(ori)
        print(count)
        
        
    result=kr.readline()
    ori = origin.readline()

kr.close()

FileNotFoundError: [Errno 2] No such file or directory: './aihub.mecab.shuf_01'

In [78]:
kr = open('./aihub.mecab.shuf_02', "r" , encoding = "utf-8")
origin = open('./아카이브/aihub.kr.shuf', "r" , encoding = "utf-8")


부호 = ['.', '?', '!', ')', '"', '…', '”', '．', ':', '~', ']', '┃', ',', '」']

요 = 0
다 = 0
까 = 0
나머지 = 0
count = 0

result=kr.readline()
ori = origin.readline()


    
while True:

    count = count+1
    
    result = result.replace('\n','')
    ori = ori.replace('\n','')
    if not result: break
    
    if 'ㅂ니다' in result:
        
        print(result)
        print(ori)
        print(count)
        
        
    result=kr.readline()
    ori = origin.readline()

kr.close()

In [41]:
kr = open('./aihub.mecab.shuf_01', "r" , encoding = "utf-8")
origin = open('./aihub.mecab.shuf', "r" , encoding = "utf-8")


부호 = ['.', '?', '!', ')', '"', '…', '”', '．', ':', '~', ']', '┃', ',', '」']

요 = 0
다 = 0
까 = 0
나머지 = 0
count = 0

result=kr.readline()
ori = origin.readline()


    
while True:

    
    
    result = result.replace('\n','')
    ori = ori.replace('\n','')
    if not result: break
    
    if 'ㅂ니다' in result:
        count = count+1
        print(result)
        print(ori)
        print(count)
        
        
    result=kr.readline()
    ori = origin.readline()

kr.close()

이정임 선임연구위원은 “수도권매립지 매립량을 줄이기 위해서는 매립량의 80%를 차지하는 건설·사업장폐기물의 관리가 무엇보다 중요하.”면서,ㅂ니다 사업장폐기물 매립 감소 방안을 수립하고 감량 및 재활용을 위한 정책 개발과 지속적인 목표관리를 언급했습니다.
이정임 선임연구위원은 “수도권매립지 매립량을 줄이기 위해서는 매립량의 80%를 차지하는 건설·사업장폐기물의 관리가 무엇보다 중요하.”면서,ㅂ니다 사업장폐기물 매립 감소 방안을 수립하고 감량 및 재활용을 위한 정책 개발과 지속적인 목표관리를 언급했습니다.
1
“차를 ‘제품’으로 전달하기보다는, 차가 있는 라이프스타일과 새로운 문화를 보여주고 싶었.”ㅂ니다 지난 1일 만난 이은빈 알디프 대표는 자신을 ‘차 덕후’였다고 일컫습니다.
“차를 ‘제품’으로 전달하기보다는, 차가 있는 라이프스타일과 새로운 문화를 보여주고 싶었.”ㅂ니다 지난 1일 만난 이은빈 알디프 대표는 자신을 ‘차 덕후’였다고 일컫습니다.
2
“젊었을 때는 무지개가 있다고 믿고 좇았으나 세월이 흐르고 나서 보니 무지개가 없다는 것을 알았.”ㅂ니다 자신이 만들어 낸 소득주도성장정책이 허상이었음을 뒤늦게 실토한 셈입니다.
“젊었을 때는 무지개가 있다고 믿고 좇았으나 세월이 흐르고 나서 보니 무지개가 없다는 것을 알았.”ㅂ니다 자신이 만들어 낸 소득주도성장정책이 허상이었음을 뒤늦게 실토한 셈입니다.
3
“투기 목적의 취득은 전혀 아니.”ㅂ니다 농지 취득 절차상의 문제를 인정하거나 무엇이 문제인지조차 모르는 의원들이 뒤섞인 가운데 이들은 모두 재산 증식의 목적은 아니라고 부인했습니다.
“투기 목적의 취득은 전혀 아니.”ㅂ니다 농지 취득 절차상의 문제를 인정하거나 무엇이 문제인지조차 모르는 의원들이 뒤섞인 가운데 이들은 모두 재산 증식의 목적은 아니라고 부인했습니다.
4
“박근혜 때가 나았.”ㅂ니다 아베 신조 일본 총리가 며칠 전 우리 정부의 화해·치유재단 해산 결정과 관련해 했다는 말입니다.
“박근혜 때가 나았.”ㅂ니다 아베 신조 일본 총리가 며칠 전 우리 정

“과학은 조국이 없지만 과학자는 조국이 있.”ㅂ니다 프랑스의 화학자 루이 파스퇴르(1822∼1895)는 보불전쟁 발발 이후 프로이센 국왕으로부터 받은 훈장을 돌려보내며 이같이 말했습니다.
“과학은 조국이 없지만 과학자는 조국이 있.”ㅂ니다 프랑스의 화학자 루이 파스퇴르(1822∼1895)는 보불전쟁 발발 이후 프로이센 국왕으로부터 받은 훈장을 돌려보내며 이같이 말했습니다.
45
“촛불혁명의 완성은 개헌이.”ㅂ니다 한때 민주당의 최대 유행어였으나 6·13 지방선거 압승 후 좀처럼 들을 수 없는 말이 되어버렸습니다.
“촛불혁명의 완성은 개헌이.”ㅂ니다 한때 민주당의 최대 유행어였으나 6·13 지방선거 압승 후 좀처럼 들을 수 없는 말이 되어버렸습니다.
46
“내 육신은 쇠잔해져도 주님께서 기뻐하신다면 내 몸을 드리겠.”ㅂ니다 안씨는 이무하씨가 부른 ‘땅 끝에서’란 곡의 가사가 삶의 고백이 되길 늘 기도했습니다.
“내 육신은 쇠잔해져도 주님께서 기뻐하신다면 내 몸을 드리겠.”ㅂ니다 안씨는 이무하씨가 부른 ‘땅 끝에서’란 곡의 가사가 삶의 고백이 되길 늘 기도했습니다.
47
광주형 일자리는 제조업 위기에서 불거진 지역경제 붕괴, 일자리 절벽 상황을 돌파하기 위해 시작된 ‘상생형 일자리’ㅂ니다.
광주형 일자리는 제조업 위기에서 불거진 지역경제 붕괴, 일자리 절벽 상황을 돌파하기 위해 시작된 ‘상생형 일자리’ㅂ니다.
48
“너희가 비판하는 그 비판으로 너희가 비판을 받을 것이.”(2절)ㅂ니다 여기서 주님이 말씀하시는 두 번째의 판단은 훗날 심판의 보좌 앞에서 당할 심판을 말씀하십니다.
“너희가 비판하는 그 비판으로 너희가 비판을 받을 것이.”(2절)ㅂ니다 여기서 주님이 말씀하시는 두 번째의 판단은 훗날 심판의 보좌 앞에서 당할 심판을 말씀하십니다.
49
“말은 곧 정신입니다.” “한 사람의 열 걸음보다 열 사람의 한 걸음이 더 크.”ㅂ니다 등 영화 속 명대사들은 영화의 메시지를 잘 전해줍니다.
“말은 곧 정신입니다.” “한 사람의 열 걸음보다 열 사람의 한 걸음이 더 크

‘신공항 백지화, 정부는 지방을 버렸.’ㅂ니다 정부가 대구나 부산 등 특정 지역이 아니라 국토의 고른 발전을 외면했다는 점을 지적했습니다.
‘신공항 백지화, 정부는 지방을 버렸.’ㅂ니다 정부가 대구나 부산 등 특정 지역이 아니라 국토의 고른 발전을 외면했다는 점을 지적했습니다.
92
올해 인증제 심사에 참여한 공공디자인위원회 김현중 위원은 “업체에서 지향하는 과도한 디자인은 인증제의 취지에서 벗어나고, 그로 인해 제품의 단가를 상승시켜 경쟁력이 위축되.”며,ㅂ니다 디자인닥터와 업체에게 적극적인 협조를 당부했습니다.
올해 인증제 심사에 참여한 공공디자인위원회 김현중 위원은 “업체에서 지향하는 과도한 디자인은 인증제의 취지에서 벗어나고, 그로 인해 제품의 단가를 상승시켜 경쟁력이 위축되.”며,ㅂ니다 디자인닥터와 업체에게 적극적인 협조를 당부했습니다.
93
‘교사는 성관계 경험이 있는 학생에 대하여 편견을 가져서는 아니 되.’ㅂ니다 ‘학교는 학생의 성인권교육을 정기적으로 실시해야 하.’ㅂ니다 경남학생인권조례 제17조에 들어있는 문구입니다.
‘교사는 성관계 경험이 있는 학생에 대하여 편견을 가져서는 아니 되.’ㅂ니다 ‘학교는 학생의 성인권교육을 정기적으로 실시해야 하.’ㅂ니다 경남학생인권조례 제17조에 들어있는 문구입니다.
94
이런 그의 정치철학 연구가 집약된 저서가 바로 <정의의 아이디어>ㅂ니다.
이런 그의 정치철학 연구가 집약된 저서가 바로 <정의의 아이디어>ㅂ니다.
95
‘자체 경쟁력을 높이는 데 집중하고, 이후 조직이 안정되면 필요에 따라 M&A를 고려할 수 있.’ㅂ니다 이는 신세계그룹이 현재 외부와 공유하고 있는 온라인 신설법인 초기 경영 계획입니다.
‘자체 경쟁력을 높이는 데 집중하고, 이후 조직이 안정되면 필요에 따라 M&A를 고려할 수 있.’ㅂ니다 이는 신세계그룹이 현재 외부와 공유하고 있는 온라인 신설법인 초기 경영 계획입니다.
96
“생식기에도 별의별 아름다움이 다 있.”ㅂ니다 다른 유인원보다 작은 송곳니 등은 남성의 폭력적 성향이 여성의 선호를 

‘내가 배울 과목 내가 선택하!’ㅂ니다 학교가 지정해준 과목대로 배우는 걸 당연하게 여겼던 학생들에게 갑자기 과목 선택지가 넓어졌습니다.
‘내가 배울 과목 내가 선택하!’ㅂ니다 학교가 지정해준 과목대로 배우는 걸 당연하게 여겼던 학생들에게 갑자기 과목 선택지가 넓어졌습니다.
146
서울특별시 노원구립 체육시설 설치 및 운영에 관한 조례 제6조제6항에 “구청장은 제6조제1항에 의한 사용자가 체육시설 사용료 등 납부에 지역화폐를 사용하게 할 수 있으며, 세부내용은 서울특별시 노원구 지역화폐 운영에 관한 조례에서 정하는 바에 따르.”ㅂ니다 규정을 신설합니다.
서울특별시 노원구립 체육시설 설치 및 운영에 관한 조례 제6조제6항에 “구청장은 제6조제1항에 의한 사용자가 체육시설 사용료 등 납부에 지역화폐를 사용하게 할 수 있으며, 세부내용은 서울특별시 노원구 지역화폐 운영에 관한 조례에서 정하는 바에 따르.”ㅂ니다 규정을 신설합니다.
147
“재판 거래를 인정할 자료나 정황은 발견하지 못했.”ㅂ니다 안철상 법원행정처장이 지난 17일 국회 업무보고에서 한 발언입니다.
“재판 거래를 인정할 자료나 정황은 발견하지 못했.”ㅂ니다 안철상 법원행정처장이 지난 17일 국회 업무보고에서 한 발언입니다.
148
이승열 센터장은 “앞으로 학교 밖 청소년들이 꿈을 키우고 건강한 사회인으로 성장할 수 있도록 청소년 정책과 지원에 힘쓰겠.”ㅂ니다 고 밝혔습니다.
이승열 센터장은 “앞으로 학교 밖 청소년들이 꿈을 키우고 건강한 사회인으로 성장할 수 있도록 청소년 정책과 지원에 힘쓰겠.”ㅂ니다 고 밝혔습니다.
149
이번 코스모폴리탄의 윤아 사진과 기사에 아랍에미리트의 현지 팬들은 “우리는 아무것도 한 것이 없는데 한국의 유명한 사람들이 아랍에미리트로 오고 있.”ㅂ니다 등의 댓글을 달며 흥분하는 모습을 보였습니다
이번 코스모폴리탄의 윤아 사진과 기사에 아랍에미리트의 현지 팬들은 “우리는 아무것도 한 것이 없는데 한국의 유명한 사람들이 아랍에미리트로 오고 있.”ㅂ니다 등의 댓글을 달며 흥분하는 

‘성경에 적혀 있는 말씀이 사실이라면 이 사람들의 말에 기죽어 주저앉으면 안 되겠.’ㅂ니다 한술 더 떠서 이렇게 선포했습니다.
‘성경에 적혀 있는 말씀이 사실이라면 이 사람들의 말에 기죽어 주저앉으면 안 되겠.’ㅂ니다 한술 더 떠서 이렇게 선포했습니다.
205
권리보호요청은 7일(초일은 산입하되, 공휴일·토요일은 산입하지 아니하.)ㅂ니다 이내에 처리함을 원칙으로 합니다.
권리보호요청은 7일(초일은 산입하되, 공휴일·토요일은 산입하지 아니하.)ㅂ니다 이내에 처리함을 원칙으로 합니다.
206
“오늘날 사법부의 현실과 국민이 염원하는 사법부의 모습에 간극이 있음을 무겁게 인식하고 있.”ㅂ니다 박상기 법무부 장관은 한발 더 나아갔습니다.
“오늘날 사법부의 현실과 국민이 염원하는 사법부의 모습에 간극이 있음을 무겁게 인식하고 있.”ㅂ니다 박상기 법무부 장관은 한발 더 나아갔습니다.
207
“음악은 어쨌거나 만국 공통의 언어이.”ㅂ니다 조시의 말을 빌리자면 케이팝 팬들은 유튜브 등의 비디오를 통해 자연스럽게 케이 뷰티로 이동합니다.
“음악은 어쨌거나 만국 공통의 언어이.”ㅂ니다 조시의 말을 빌리자면 케이팝 팬들은 유튜브 등의 비디오를 통해 자연스럽게 케이 뷰티로 이동합니다.
208
시장은 「산업입지 및 개발에 관한 법률 시행령」(이하 “시행령”이라 하.)ㅂ니다 제42조의3제5항에 따라 다음 각 호의 어느 하나에 해당하는 기업을 대상으로 산업시설용지를 우선 분양받게 할 수 있습니다.
시장은 「산업입지 및 개발에 관한 법률 시행령」(이하 “시행령”이라 하.)ㅂ니다 제42조의3제5항에 따라 다음 각 호의 어느 하나에 해당하는 기업을 대상으로 산업시설용지를 우선 분양받게 할 수 있습니다.
209
“도시 불빛을 이불 삼고 지내는 이 사람들은 방이 아니라 집이 필요하.”ㅂ니다 함께 외친 구호는 짧지만, 큰 울림으로 퍼졌습니다.
“도시 불빛을 이불 삼고 지내는 이 사람들은 방이 아니라 집이 필요하.”ㅂ니다 함께 외친 구호는 짧지만, 큰 울림으로 퍼졌습니다.
210
방콕 택시에 대한 

“뭔가 지칠 만하면 일 년에 한 번씩 상을 타니까, 그 상이 용기를 갖고 계속 가게 하는 동력이 됐.”ㅂ니다 초콜릿 메이커 부부의 결론은 간명합니다.
“뭔가 지칠 만하면 일 년에 한 번씩 상을 타니까, 그 상이 용기를 갖고 계속 가게 하는 동력이 됐.”ㅂ니다 초콜릿 메이커 부부의 결론은 간명합니다.
253
‘셰프 복장을 한 남성이 싱싱한 생선을 손질하.’ㅂ니다 ‘무용복을 입은 여성과 남성이 무대 위에서 춤을 추.’ㅂ니다 ‘운동복 차림의 주인공이 스트레칭 시범을 보이.’ㅂ니다 식당이나 공연장 등을 상상해볼 테지만 정답은 아닙니다.
‘셰프 복장을 한 남성이 싱싱한 생선을 손질하.’ㅂ니다 ‘무용복을 입은 여성과 남성이 무대 위에서 춤을 추.’ㅂ니다 ‘운동복 차림의 주인공이 스트레칭 시범을 보이.’ㅂ니다 식당이나 공연장 등을 상상해볼 테지만 정답은 아닙니다.
254
‘손바닥을 마주쳐야 소리가 나.’,ㅂ니다 ‘탱고를 추는 데는 2명이 필요하.’ㅂ니다 북-미 협상이 어려움에 처할 때마다 빠짐없이 등장하는 표현입니다.
‘손바닥을 마주쳐야 소리가 나.’,ㅂ니다 ‘탱고를 추는 데는 2명이 필요하.’ㅂ니다 북-미 협상이 어려움에 처할 때마다 빠짐없이 등장하는 표현입니다.
255
이인진 전시감독은 “이번과 같은 작가 지명공모 방식은 비엔날레의 주제와 형식에 더 집중하여 기획의도를 효과적으로 부각시켜 경기세계도자비엔날레가 세계 도예계 흐름을 주도하는데 크게 기여할 것이.”ㅂ니다 고 말했습니다.
이인진 전시감독은 “이번과 같은 작가 지명공모 방식은 비엔날레의 주제와 형식에 더 집중하여 기획의도를 효과적으로 부각시켜 경기세계도자비엔날레가 세계 도예계 흐름을 주도하는데 크게 기여할 것이.”ㅂ니다 고 말했습니다.
256
‘물고기도 느낄 것 다 느끼고 알 것 다 아.’ㅂ니다 물고기와 우리가 ‘노는 물’이 달라서 소통을 못 했을 뿐이지, 물고기가 자기 생각이나 감정이 없었던 것이 아니었습니다.
‘물고기도 느낄 것 다 느끼고 알 것 다 아.’ㅂ니다 물고기와 우리가 ‘노는 물’이 달라서 소통을 

기존의 우중충한 던전에서 탈피해 아기자기한 애니메이션 캐릭터와 게임 그래픽으로 글로벌 시장에서 두각을 나타낸 모바일 게임이 ‘던전메이커’ㅂ니다.
기존의 우중충한 던전에서 탈피해 아기자기한 애니메이션 캐릭터와 게임 그래픽으로 글로벌 시장에서 두각을 나타낸 모바일 게임이 ‘던전메이커’ㅂ니다.
300
“신용카드는 부자를 위한 것이고, 모바일결제는 가난한 사람을 위한 것이.”ㅂ니다 마윈 알리바바 회장이 2019년 1월24일 스위스 다보스포럼에서 한 말입니다.
“신용카드는 부자를 위한 것이고, 모바일결제는 가난한 사람을 위한 것이.”ㅂ니다 마윈 알리바바 회장이 2019년 1월24일 스위스 다보스포럼에서 한 말입니다.
301
서울특별시 노원구 평생교육진흥 조례 제18조제4항에 “구청장은 제18조 제1항의 평생교육 프로그램 이용자가 수강료 납부에 지역화폐를 사용하게 할 수 있으며, 세부내용은 서울특별시 노원구 지역화폐 운영에 관한 조례에서 정하는 바에 따르.”ㅂ니다 규정을 신설합니다.
서울특별시 노원구 평생교육진흥 조례 제18조제4항에 “구청장은 제18조 제1항의 평생교육 프로그램 이용자가 수강료 납부에 지역화폐를 사용하게 할 수 있으며, 세부내용은 서울특별시 노원구 지역화폐 운영에 관한 조례에서 정하는 바에 따르.”ㅂ니다 규정을 신설합니다.
302
“이 세상 모든 사람들은 다 작가.”ㅂ니다 서정오 작가는 ‘내 인생의 글쓰기’라는 책에서 직업 작가만이 아니라 세상 모든 사람들이 자신의 이야기를 풀어내는 글을 써야 한다고 강조했습니다.
“이 세상 모든 사람들은 다 작가.”ㅂ니다 서정오 작가는 ‘내 인생의 글쓰기’라는 책에서 직업 작가만이 아니라 세상 모든 사람들이 자신의 이야기를 풀어내는 글을 써야 한다고 강조했습니다.
303
‘언니가 돌아왔.’ㅂ니다 지은희(33)가 미국여자프로골프(LPGA) 투어 시즌 개막전에서 우승하며 박세리(42)가 갖고 있던 한국인 LPGA 최고령 우승 기록을 새로 수립했습니다.
‘언니가 돌아왔.’ㅂ니다 지은희(33)가 미국여자프로골프(LPGA) 투

폴이 제 아무리 일인칭에서 이인칭으로 삼인칭으로 널뛰기를 한다 해도, 옮긴이 정영목이 지적한 대로, 이 이야기에 “또 한 사람의 이야기는 텅 비어 있”ㅂ니다.
폴이 제 아무리 일인칭에서 이인칭으로 삼인칭으로 널뛰기를 한다 해도, 옮긴이 정영목이 지적한 대로, 이 이야기에 “또 한 사람의 이야기는 텅 비어 있”ㅂ니다.
345
“거리보다 난 친구도 할 일도 많.”ㅂ니다 당시에는 이 말이 무슨 의미이고 어떤 변화가 따를지 전혀 예측하지 못했습니다.
“거리보다 난 친구도 할 일도 많.”ㅂ니다 당시에는 이 말이 무슨 의미이고 어떤 변화가 따를지 전혀 예측하지 못했습니다.
346
‘사자도 물속에서는 새우에 뜯어먹히고 바다의 지배자 상어가 뭍에 나오면 개미의 먹이일 뿐이.’ㅂ니다 젊은 인재의 양성과 적재적소 활용은 동서고금을 떠나 조직 운용의 기본입니다.
‘사자도 물속에서는 새우에 뜯어먹히고 바다의 지배자 상어가 뭍에 나오면 개미의 먹이일 뿐이.’ㅂ니다 젊은 인재의 양성과 적재적소 활용은 동서고금을 떠나 조직 운용의 기본입니다.
347
선부역 5번 출입구를 나와 공원을 가로질러 나오면 삼성디지털 프라자 선부점 옆 3층짜리 큰 건물이 바로 ‘갈비이야기’ㅂ니다.
선부역 5번 출입구를 나와 공원을 가로질러 나오면 삼성디지털 프라자 선부점 옆 3층짜리 큰 건물이 바로 ‘갈비이야기’ㅂ니다.
348
진리를 위해 생명을 걸고 참 사랑이 무엇인지 보여주신 예수님, ‘한 영혼이 온 천하보다 귀하.’ㅂ니다 이 말씀을 붙들고 부드럽게 전진합니다.
진리를 위해 생명을 걸고 참 사랑이 무엇인지 보여주신 예수님, ‘한 영혼이 온 천하보다 귀하.’ㅂ니다 이 말씀을 붙들고 부드럽게 전진합니다.
349
“보행은 몸과 마음과 세상이 한편이 된 상태.”ㅂ니다 그런데 이 책에서 보행의 감동을 묘사한 백미는 소설가 김연수의 추천사라고 할 수 있습니다.
“보행은 몸과 마음과 세상이 한편이 된 상태.”ㅂ니다 그런데 이 책에서 보행의 감동을 묘사한 백미는 소설가 김연수의 추천사라고 할 수 있습니다.
350
이 규칙

사람을 향한 예민한 감성과 특유의 따스함이 느껴져 보좌진으로서는 ‘괜찮은 정치인과 일하고 있어 참 좋.’ㅂ니다 라고 생각할 수 있었습니다.
사람을 향한 예민한 감성과 특유의 따스함이 느껴져 보좌진으로서는 ‘괜찮은 정치인과 일하고 있어 참 좋.’ㅂ니다 라고 생각할 수 있었습니다.
392
조사를 담당하는 세무부서장이 법 제84조제1항에 따라 조사기간을 연장하려면 납세자보호관에게 조사기간 종료 3일(공휴일·토요일 제외, 이하 이 조에서 같.)ㅂ니다 전까지 신청하여야 합니다.
조사를 담당하는 세무부서장이 법 제84조제1항에 따라 조사기간을 연장하려면 납세자보호관에게 조사기간 종료 3일(공휴일·토요일 제외, 이하 이 조에서 같.)ㅂ니다 전까지 신청하여야 합니다.
393
서울특별시 구로구청장(이하 “구청장”이라 하.)은습니다 구로구(이하 “구”라 하.)ㅂ니다 내 태양광 등 재생에너지를 이용한 공공조명 설치 및 보급 지원에 필요한 시책을 마련하여 사업을 추진할 수 있습니다.
서울특별시 구로구청장(이하 “구청장”이라 하.)은습니다 구로구(이하 “구”라 하.)ㅂ니다 내 태양광 등 재생에너지를 이용한 공공조명 설치 및 보급 지원에 필요한 시책을 마련하여 사업을 추진할 수 있습니다.
394
“(말은) 기독교도 기마병들이 소수의 인원으로도 2500만명 이상의 사람들이 살고 있던 신세계를 손쉽게 정복할 수 있게 해줬.”ㅂ니다 고향으로 돌아온 말은 아메리카 원주민에게 재앙이었습니다.
“(말은) 기독교도 기마병들이 소수의 인원으로도 2500만명 이상의 사람들이 살고 있던 신세계를 손쉽게 정복할 수 있게 해줬.”ㅂ니다 고향으로 돌아온 말은 아메리카 원주민에게 재앙이었습니다.
395
“일개인이 스스로 활동하여 독립하면 일 가정이 자활독립하고 일국이 자활독립하니 일개인의 영향이 국가와 관계가 있다고 하지 않을 수 없.”ㅂ니다 이러한 논리는 이른바 자조론(自助論), 자강론(自强論)으로 이어집니다.
“일개인이 스스로 활동하여 독립하면 일 가정이 자활독립하고 일국이 자활독립하니 일개인의 영향이 국

“미술은 보이는 것을 표현하는 것이 아니라 어떤 것을 보이게 하는 것이.”ㅂ니다 화가 파울 클레의 말을 빗대어 견(見)을 하지 말고 관(觀)을 하라는 소리였습니다.
“미술은 보이는 것을 표현하는 것이 아니라 어떤 것을 보이게 하는 것이.”ㅂ니다 화가 파울 클레의 말을 빗대어 견(見)을 하지 말고 관(觀)을 하라는 소리였습니다.
440
“성공은 나이가 들어서 주위에 사람들이 많이 있는 것이.”ㅂ니다 나이가 들어서도 젊은 사람들이 함께하고 싶어하고 배우고 싶어하는 어른이 되는 것이 성공이라는 것입니다.
“성공은 나이가 들어서 주위에 사람들이 많이 있는 것이.”ㅂ니다 나이가 들어서도 젊은 사람들이 함께하고 싶어하고 배우고 싶어하는 어른이 되는 것이 성공이라는 것입니다.
441
300명의 현지인에게 한국어 교실을 통해 한국어를 가르치고 있는 엄인경 K-POP Station 대표는 “평소에 가르쳤던 학생 중 두 명이 수상하여 한국에서 공부할 수 있게 되어 큰 보람을 느끼.”ㅂ니다 라고 인터뷰했습니다.
300명의 현지인에게 한국어 교실을 통해 한국어를 가르치고 있는 엄인경 K-POP Station 대표는 “평소에 가르쳤던 학생 중 두 명이 수상하여 한국에서 공부할 수 있게 되어 큰 보람을 느끼.”ㅂ니다 라고 인터뷰했습니다.
442
이 규칙은 인천광역시 서구(소속기관 및 하부행정기관을 포함하.)ㅂ니다 또는 서구청장을 당사자로 하는 소송사건과 공무원으로서 수행한 직무관련사건의 수행 절차와 업무 범위를 규정함을 목적으로 합니다.
이 규칙은 인천광역시 서구(소속기관 및 하부행정기관을 포함하.)ㅂ니다 또는 서구청장을 당사자로 하는 소송사건과 공무원으로서 수행한 직무관련사건의 수행 절차와 업무 범위를 규정함을 목적으로 합니다.
443
서울특별시 노원구 목공예체험장 운영 및 관리 조례 제10조제4항에 “구청장은 제10조제1항의 체험자가 사용료의 납부에 지역화폐를 사용하게 할 수 있으며, 세부내용은 서울특별시 노원구 지역화폐 운영에 관한 조례에 따르.”ㅂ니다 규정을 신설합니다.
서울특

In [80]:
kr = open('./aihub.mecab.shuf_01', "r" , encoding = "utf-8")
origin = open('./aihub.mecab.shuf_02', "r" , encoding = "utf-8")


부호 = ['.', '?', '!', ')', '"', '…', '”', '．', ':', '~', ']', '┃', ',', '」']

요 = 0
다 = 0
까 = 0
나머지 = 0
count = 0

result=kr.readline()
ori = origin.readline()


    
while True:

    
    
    result = result.replace('\n','')
    ori = ori.replace('\n','')
    if not result: break
    
    if result !=ori:
        count = count+1
        print('')
        print(result)
        print(ori)
        print(count)
        
        
    result=kr.readline()
    ori = origin.readline()

kr.close()


이정임 선임연구위원은 “수도권매립지 매립량을 줄이기 위해서는 매립량의 80%를 차지하는 건설·사업장폐기물의 관리가 무엇보다 중요하.”면서,ㅂ니다 사업장폐기물 매립 감소 방안을 수립하고 감량 및 재활용을 위한 정책 개발과 지속적인 목표관리를 언급했습니다.
이정임 선임연구위원은 “수도권매립지 매립량을 줄이기 위해서는 매립량의 80%를 차지하는 건설·사업장폐기물의 관리가 무엇보다 중요하.”면섭니다, 사업장폐기물 매립 감소 방안을 수립하고 감량 및 재활용을 위한 정책 개발과 지속적인 목표관리를 언급했습니다.
1

‘대체복무기간도 현역복무와 똑같아야 하.’,ㅂ니다 ‘봉사활동으로 다양한 항목을 주고 유연하게 선택할 수 있게 해야 합니다.’ 등 대체복무에 대한 4심 위원들의 다양한 의견들이 오고 갔습니다.
‘대체복무기간도 현역복무와 똑같아야 합니다.’, ‘봉사활동으로 다양한 항목을 주고 유연하게 선택할 수 있게 해야 합니다.’ 등 대체복무에 대한 4심 위원들의 다양한 의견들이 오고 갔습니다.
2

도 기업지원과 관계자는 “지난 12월 30일 발표된 정부의 AI 특별자금 융자지원 계획이 소상공인 중심으로 되어 있어 이에 제외된 중소기업을 중심으로 자체 지원계획을 수립했.”며,ㅂ니다 적극적인 관심을 당부했습니다.
도 기업지원과 관계자는 “지난 12월 30일 발표된 정부의 AI 특별자금 융자지원 계획이 소상공인 중심으로 되어 있어 이에 제외된 중소기업을 중심으로 자체 지원계획을 수립했.”몁니다, 적극적인 관심을 당부했습니다.
3

“가난한 사람이 경작한 밭에서는 많은 소출이 날 수도 있으나 불의가 판을 치면 그에게 돌아갈 몫이 없.”(13:23,ㅂ니다 새번역) 정규직을 꿈꾸며 열심히 일하던 비정규직 청년이 불의한 구조로 모든 것을 잃게 된 것입니다.
“가난한 사람이 경작한 밭에서는 많은 소출이 날 수도 있으나 불의가 판을 치면 그에게 돌아갈 몫이 없습니다.”(13:23, 새번역) 정규직을 꿈꾸며 열심히 일하던 비정규직 청년이 불의한 구조로 모든 것을 잃게 된 것입니다.
4



In [82]:
kr = open('./aihub.mecab.shuf_02', "r" , encoding = "utf-8")

부호 = ['.', '?', '!', ')', '"', '…', '”', '．', ':', '~', ']', '┃', ',', '」']

요 = 0
다 = 0
까 = 0
나머지 = 0

result=kr.readline()

while(result != ''):
    

    
    result = result.replace('\n','')
    while result[-1] in 부호:
            result= result[:-1].strip()
    
    if result[-1] == '요' or result[-1] == '죠':
        요+=1
    elif result[-1] == '다':
        다+=1
    elif result[-1] == '까':
        까+=1
    else:
        나머지+=1
        print(result)
        
    result=kr.readline()

kr.close()

을지로는 확실히 회사들이 많아서 점심시간에 줄을 너무 오래 서야 해
파티에 가서 즐겁게 놀아라, 헤더야
깜짝 놀라게 해주고 싶어서 며칠 전부터 몰래 준비했어
먼저 이메일로 너희 제품의 단가표를 받아보고 싶어
사. 가목부터 마목까지에 해당하는 경우로서 기존 투자법인이 「산업집적활성화 및 공장설립에 관한 법률」에 따라 공장을 증설하는 사업
그러면 지금 있는 약들 다시 체크해 보고 넉넉하게 구매해서 챙겨드려
천재지변, 기타 불가항력적인 사유로 사용이 불가능한 경우 : 사용료의 전액
결혼하고 난 후 여자는 일과 육아를 함께해야 하므로 아직 한국에서는 여자가 성공하기엔 힘들어
이놈의 똥컴 진짜 느려 터져서 답답해 죽겠네
너한테 데이트 신청하는 남자들 없잖아
그것이 조금도 놀랍지가 않단 말이야
한국, 미국, 그리고 필리핀 연결할 수 있는 은행 통장 만들어
어제 일찍 잠들어서 메시지도 못 보내서 미안해
팀은 시간여행능력을 쓰지 않고도 현실에 행복 해질 수 있다는 것을 알게 돼
현재와 미래의 기술로 어떤 사회를 만들 수 있을지에 대한 얘기들이 모든 언론 매체에 흘러넘치게 만들자
그 장학금은 아무나 다 지원해서 받을 수 있는 거야
그에게 사격 훈련 장애물 훈련, 차량 훈련 등을 훈련시켜
아니, 오늘 일요일이라서 난 교회에 갔다 왔어
솔직히 처음에는 관심 반, 장난반 으로 시작했어
백화점 1층으로 내려가면 택시를 타는 곳이 있어
나는 내가 지금까지 하지 못했던 것을 하기를 원했었어
주변을 아무리 둘러봐도 길을 잘 모르겠어
안타깝지만 우리는 Bar 공간이 충분치 않아
우리 다음에 함께 좋은 시간 보내자
말을 정말 착하게 해 주시는군요, 애로우 씨
두려울 때일수록 더 욕심을 내라
만일, 화산 계란찜에 만드는 것에 실패하였더라도 낙담하지 말고 다시 도전해봐
왜 이렇게 외국인이 많은가 했더니 한복 체험 때문이었구나
네 다음 남자 친구는 좋은 사람 일 거야
러시아의 모든 핵 발사 사일로와 이동식 발사대에 경보가 걸렸고, 마침 그가 관제센터의 당직이었어
동원아, 네가 얼마 전에 목표가 왜

내가 처음 해 본 대형 프로젝트였고 청소년 때 했던 일 중 가장 기억에 남아
응, 다른 날은 내가 안 돼서 그날 하는 게 좋을 것 같아
그들이 찾은 것들과 그림들은 매우 오래된 것이었어
혼자 자취하면 아무래도 식비가 많이 나가게 되지
정말? 그 영화 보러 가고 싶습니다. 같이 갈래
너희가 생산하는 기본 색 에서 우리가 원하는 색상으로 변경이 가능해
내 생각엔 네가 번호를 잘못 받은 거 같아
지방세 납부사항 및 체납여부 조회 의뢰에 대한 회신
우리가 송금할 수 있도록 인보이스 보내줘
그녀의 자살은 우리를 충격에 빠뜨렸어
내가 받은 카드 중 너의 것이 제일 이뻐
나는 선생님이 내 앞에 있을 때 긴장돼
내 생각에 43번 게이트와 47번 게이트 인근에서 잃어버린 것 같아
우리는 미국 가기 전후로 태국에 갈 수 있어
옷 가게 안에 커피숍을 차리고 싶어
나는 네가 좋은 간호사가 될 거라고 기대해
너 밤에는 일하고 낮에는 학교 다니는 거야
보통 교통비, 숙박비, 활동비 정도는 여비교통비로 적용되겠지
내가 가장 좋아하는 텔레비전 프로그램은 상속자들이야
그래서 우리는 대화를 자주 하기 힘들어
우리가 자랑스럽게 말할 수 있는 것은, 네가 최고의 매니저라는 거야
미리 환전하는 걸 잘 챙기라고 했는데 결국 까먹다니
행위의 이유와 진실의 여부를 떠나 사람들은 씹을 누군가가 필요한 거야
추석이 길어서 하고 싶은 걸 많이 할 수 있어서 좋았어
최대 난 너에게 하루를 무료로 줄 수 있어
야근해도 우리 오늘 만날 거야
너 종아리 알 보톡스 맞은 거 효과는 보고 있어
우리의 감정이 태도가 되도록 하지는 말자고
나는 자신의 상황에 굴하지 않는 레미가 멋있다고 생각해
당신은 제 패션에 관심이 있어서 이걸 사는 거잖아
내가 예능 방송들은 대부분 아는데, 이 방송은 처음 보는데
네가 일 끝나고 바로 집으로 오면 좋겠어
나는 비키니랑 좋아하는 영화들을 챙길게
맛있게 먹긴 했는데 솔직히 약간 비린 맛 났어
나는 미술에는 별로 관심이 안 가는데 너 혼자 가서 보고 올래
갑자기 집에서 왜 운동하려고 하니


나 아직 샤워도 안 했는데
나는 할리우드 영화보다 한국 영화를 더 좋아해
여기서 이러지 말고 다른 곳으로 도망쳐
정말 물리치료를 잘하시는 것 같아요, 다른 데서는 별로 효과를 못 봤는데
내가 보낸 것들에 대해서 간단히 설명할게
나의 어릴 적 꿈은 사회복지사였어
영업팀 매니저님이 회사 카드를 개인적인 용도로 사용했대
그런 다음에 이것을 찾아봐
내 말은 네가 한국에 있는 동안 아주 바빠서 식사만 하고 헤어지더라도 자주 봤으면 좋겠다는 말이야
아니 나는 늑대인데 당연히 고기를 먹어야지
약속을 지키지 못할 이런저런 핑계 대지 마
저쪽 책상 옆에 하나 있는 것 같아
노원평생교육원에 등록된 학습동아리가 직접 학습목적으로 사용하는 경우
이용자(제3조에 따라 이용 신청을 하고 이용료를 납부한 자를 말합니다. 이하 같다)가 이용 시작일 14일 전까지 이용 신청을 취소한 경우: 이용료 전액 반환
무늬야 사랑해, 우리 평생 함께하자
그래, 우리가 일요일에 만나기로 한 거 알고 있어
그러나 결국 그 일이 일어나고 말았어
나는 공부도, 널 좋아하는 마음도 포기할 수가 없어
내가 이렇게 추리소설을 좋아하기는 하지만 책을 읽는다고 해서 추리 실력이 늘지는 않는 것 같아
당신은 나와 있으면 행복 하지 않는다면 당신 행복을 찾아 떠나
야 너희 팀은 어떻게 9회에 10점 주고 역전패당하냐
너랑 함께했다는 것이 좋아
지금은 위험해서 너에게 차를 줄 수가 없어
자세한 건 토요일에 만나서 얘기하자
나는 인도 여자들이 진짜 예쁜 것 같아
내가 네게 싱가포르 현지 항공사 연락처 알려줄 테니 이 화물을 누가 보냈는지 확인해봐
너는 오디션에서 너의 장점을 알리는 것이 매우 중요해
그래, 이곳은 유명하니까 알아 두는 게 좋을 것 같아
혹시 내가 영어를 틀렸다면 말해줄래
새벽 늦게까지 밤새 친구들과 생일 파티하고 세시간 자고 아빠 보러왔어
너희가 요청하면 나는 가끔 도와줄 수 있어
기존 아르바이트생들의 텃세와 뒷말로 인해 견디지 못한 B는 한 달도 채우지 못하고 일을 그만두었어
오늘 창문 열다가 깜짝 놀랐는

너 나랑 결혼하고 싶은 생각 있어
당신에게 사용하는 돈은 전혀 아깝지 않아
나는 솔직히 이 사진이 감정에 충만하고 예쁜 감정으로 가득하다고 생각해
그러나 그는 언제나 꿈을 꾸는 사람이었어
너와 나는 영화 취향이 비슷한 것 같아
미안하지만 네가 여기서 나가줬으면 좋겠어
네가 뉴욕에서 나랑 같이 있는 동안은 안 돼
난 너를 이해하려고 노력하고 있으니까 너도 노력해줘
이 앱 속에서는 친구를 찾지 않는 것이 좋아
서울특별시 노원구 의사상자 예우 및 지원에 관한 조례
범인이 누군지 추측하는 재미가 있어
나는 페이팔로 너의 배송비를 환불했어
우리 할머니는 정차 벨 찾는 것이 꽤 힘들다고 하셨어. 이제는 그런 걱정 안 해도 될 것 같아
원래 열차 안에서는 음식을 먹을 수 있는 거 몰랐어
팀 영상에서 너의 클립을 지우는 걸 원해
그녀를 이성으로 좋아하는 것은 아니야
나는 영어를 잘하진 못하지만, 열심히 할 거야
재수생이 학생부종합전형에 지원하는 비율은 크지 않지만 작년에 1단계에서 서류가 통과한 경우 또는 수능 최저 기준을 충족하지 못해 최종 불합격했다면 과감하게 다시 도전해보자
어제 인기 검색어에 남주혁이 있던데, 모두 칭찬하고 있더라
경호원이 내가 경계선을 가로질러가는것을 막지 않고 놔뒀어
글쎄요. 외야석이 구하기는 제일 좋을 것 같은데
난 돈을 많이 벌었기 때문에 괜찮아
하지만 내가 널 여전히 필요로 한다는 걸 나는 알아
나는 그와 영화 동아리에 가입할 예정이야
우리 일정이 있기 때문에 그건 어려워
해외 출장 직전에는 모두가 부업에 열중하지
아빠가 감기에 걸려서 카누를 못 탔어
나는 치킨 너겟을 주문하려고 하는데, 무슨 햄버거 먹을래
그냥 여유 있게 공항 가서 햄버거나 하나 먹고 있자
네 답장이 늦어서 나는 자겠어야
여기 즉석식품 중에서 닭강정이랑 빵 엄청 맛있던데
하지만 우리는 객관적이고 사실적으로 판단하여 결정해야 한다는 것을 잊지 말자
그 사람의 인기를 확인해 보는 시간이야
아이들이 미술관에서 너무 뛰어다니는 것 같지 않아
외국인에게 자랑할 만한 한국 문화에 관해

나는 기다렸지만 그녀는 오지 않았어
산딸기랑 블루베리에 와플을 얹어 먹어도 좋아
나는 회사에서 연락을 할 수도 있어서 끌 수가 없어
이 도시의 크기를 고려하면, 그 정도면 괜찮은 것 아닌가
만약 네가 그의 이름을 한국어로 말 할 수 있다면 난 너에게 화내지 않겠어
강황 성분이 첨가된 분할 복합사 제조방법
나는 너가 이 고난을 지나갈 수 있도록 최선을 다해서 도왔어
고용정보를 바탕으로 장애인의 희망·적성·능력과 직종 등을 고려하여 적합한 직업 알선 및 권고
당신은 당신의 인생을 스스로 존중하십시오
그들은 어떻게 4대 1로 싸우고 질 수가 있지
재활용시설을 만들지 않으면 허가를 받을 수 없게 말이야
아직 두시밖에 안 됐어, 왜 이렇게 피곤한지 모르겠네
나는 내가 무엇을 잘하는지 생각해 보았었어
그럼 나야 정말 고맙지. 나는 5박 6일 생각하고 있어
단지 그는 잠이 너무 많아
나는 지금까지 타본 배라고는 오리배가 전부야
서비스 제공 공무원의 부서명 및 연락처 등
아마도 새벽에 도착할 것 같지 않아
가는 데 얼마 안 걸리니까 냉동도 괜찮을 거야
미리 구상하고 시안을 보여주니깐 걱정할 필요가 없어
오후 12시에 공항버스를 타면 시간이 충분하겠지
다른 섀도보다 지속력이 좋아서 좀 오래 가
하지만 열심히 만들어서 기분이 좋았어
아마도 이번 주엔 수업할 수 없을 것 같아
운전을 세 시간 동안 하니까 조금 피곤해
고장 났지만 강한 척하는 게 어떤 기분인지 나는 알아
내가 왜 나의 종교를 강요받아야 하는 거야
여행가고 싶은데 다 들 바빠서 시간이 안될 것 같아
난 우리가 서로 일이 바빠서 자주 못 만난 거 이해해
나 오늘은 방어회가 너무 당겨
아무리 그래도 30분이나 늦게 들어오는 건 용납할 수 없네
어쩌다 보니 노력하지 않는 사람이 돼버렸어
이거 내가 혼자 해 보고 싶어
원래 내일 쇼핑하기로 했었지? 어떡하면 좋지? 세일 기간을 놓치는 건 아까운데
네가 가서 현관문 좀 열어줘
근처에 엄청 맛있는 떡볶이집 찾아놨는데, 같이 가자
손님의 성함을 알려주십시오
공사범위는 담장허물기에

...

한국에 살면서 영어를 배운다는 것은 어려운 일인 것 같아
그래도 열심히 하면 좋은 결과가 있을 거야. 우리 힘내보자
고마워, 큰마음 먹고 좋은 미용실에서 머리 좀 했지
어느 남자가 듣기 위한 귀가 있다면, 듣게 하라
진리 탐구를 위한 인도자가 필요해
외국인 친구에게 다양한 한국 음식을 경험하게 하고 싶어
해당 관할 지역 이외의 지역으로 이주하였을 때
혹시 너희 회사소개 자료가 있으면 공유해줄 수 있니
면세점 옷은 쓸데없이 비싸기만 하고 돈만 아까워
내 여동생이 좋아하는 선물을 사달라고 부탁하는 거야
오늘도 즐거운 하루 되라 집에 간다 잘 있어라
기회야 만들면 되지~ 꼭 같이 연주하자
대구 여름 날씨는 서울 여름 날씨보다 훨씬 덥네
응, 이쪽으로 쭉 걸어가면 3호선 열차를 탈 수 있어
우리 숙소랑 너희 집이랑 너무 멀어
난 네가 다른 여자애들 사진에 댓글을 다는 걸 알 때마다 울적해져
잠깐만, 나는 이 여자랑 중요한 이야기를 하려고 왔어
만약 누군가 문에 노크하거나 벨을 누른다면 절대로 응답하지 마십시오
머리 다 하고 나한테 사진 보내는 거 잊지 마
너 약을 어디에 걸린 적 있어
나도 지금 자다가 화장실 가려고 깼어
그래도 좋아지지 않는다면 피부과에 가봐
요즘은 사람들이 대학을 별로 중요하게 생각하지 않아
홈쇼핑에서 한 획을 그은 에코 썬 스틱
사람들은 어른이 되면 먹고살기 위해 일을 해야 하지만, 부잣집 개가 되면 그럴 필요가 없지
가정 내 전염의 확산을 방지하기 위한 항균물질 등의 사용에 대한 위험도 평가 접근
품질 원포인트 교육 및 생산 시작 전 작업자에게 추가로 인지 교육을 해줘
나는 너를 여동생으로만 생각해야 해
너는 이 늦은 시간에 뭐 하고 있니
걱정하지 마, 너는 언제나 그랬듯 발표 잘 해낼 거야
나는 기말고사를 먼저 보고 싶어
이제 나의 발표에 집중할 준비가 되었는가
거기는 가성비가 좀 별로인 것 같은데, 다른 곳 가자
왜요? 요즘에는 레슬링 보는 사람 별로 없는데
몇십 년 뒤에 내가 설계한 집에서 살 거야
대학교 입학하고 나서부터 방학 때마다 가

우리는 아이템의 승인이 완료된 줄 알고 보냈는데
이제는 광고에도 줄거리가 있고 이야기가 있어
어떻게 하지, 시험이 9시 30분에 시작인데 9시에 일어났어
혹시 한 달에 한 번 찾아오는 고통인 거야
수입증지판매소임을 명확히 알 수 있도록 판매인 표찰(별지제 3호서식)을 게시할 것
그렇구나, 그럼 혈액순환이 잘되도록 도와준다는 얘기구나
신분증 사본은 저번에 출력해둔 거 쓰면 되겠다, 고마워
너희들은 학교 소풍으로 어디에 갔었니
이 표에서 밑에서 두번째 사람은 누구지
그들이 네 옆에 싸우기 전에 넌 그들을 해방해야만 해
그렇지? 나도 내 아들이 그렇게 물으니까 뭐라고 대답을 못 하겠더라고
당신은 다른 문의 사항이 있으시면 언제든지 서비스 핫라인으로 연락해주십시오
그는 전문가이며 여기에 몇 차례 방문한 적이 있어
김 군이 요즘 전화기에 관심이 많아
너같이 파티 좋아하는 애가 왜 파티에 가지 않니
나는 기술자의 지원을 요청합니다, 즉시
네 덕분에 우리가 이길 수 있었어
크리스마스라서 좀 신경 써서 식당 예약했는데 이게 뭐야
내 동생이 여행 가서 나한테 강아지를 맡아달라고 부탁했어
너에게 최대한 빨리 답장할 수 있도록 노력할게
차가 나무에 부딪혀서 운전자가 나무에 걸렸어
그래? 그런데도 곧잘 하는데, 전공이 뭔가
지금 비가 오고 있지 않다면 난 산책하러 갈 텐데
그것은 도대체 뭐가 그렇게 대단했니
내가 너의 일을 방해했다면 미안해
가족이랑 세부 갔다 왔는데 너무 더웠어
난 네가 매운 음식을 먹을 수 없다는 걸 몰랐어
세로 사진을 올리지 않겠다는 나만의 룰을 깨야 할 것 같아
메뉴가 너무 많아서 뭘 시켜야 할지 모르겠는데
엄마도 지금까지 제주도에 갈 땐 항상 비행기만 이용해서, 잘 몰랐는데 신기하구나
나는 여행지에 관한 내용과 날짜, 교통수단, 여행경비 등을 물어 볼 수 있어
내가 전화로 알려줄 테니까 나한테 친구 전화번호 줘봐
그들은 할 수 없다고 말했어
응, 웬만한 스포츠 경기보다 더 재밌고 긴장감 있어
지금이 너에게 생일 축하한다고 말할 알맞은 때인 것 같아
한국 같

내가 내일 이 사이트에 업데이트할게
네가 나한테 전화했을 때 이미 난 떠났었어
그러게, 우리 딸이랑 오니 이렇게 좋은 걸 왜 인제야 왔나 몰라
너의 숙제를 열심히 하려무나
네가 하는 행동 하나하나가 진심 아닌 장난이었으면 해, 그리고 어차피 상처를 줄 거면 시작도 하지 말았어야 해
당신은 늘 손에서 핸드폰을 놓고 다니지 않아
내 꿈은 바닷가 근처에 사는 거야
당신 허세를 부리지 마세요 제발
어제 내 친구는 USDA 서류를 만들었어
미안한데 어제 피곤해서 일찍 잠들었어
잘 어울린다고 하는 사람들도 많던데, 나는 조금 보기 불편하더라고
그건 네가 아까 어떤 사람한테 길을 물어봤으니까 그렇지
그래야 나중에 커서 무엇이든 잘 먹어
아까 말한 것처럼 내가 만약에 진짜로 다른 남자가 있다면 어떻게 할 건데
나하고 취향도 너무 다른데, 내 옷까지 컨트롤 하려고 해
나는 이제 오리엔테이션 끝나고 집에 가는 중이야
그럼, 우리 월요일에 첫 수업 끝나고 먹으러 가자
안녕 세레이, 난 한국인이야
만약 내가 유학을 하러 갔다면 영어를 좀 더 잘했을 텐데
그래, 네가 보내줄 사진 기대하고 있을게
바이에른에서 올라온 사람들이 많이 살았어
나는 거의 줄 끝에 매달린 느낌이었어
성년의 날을 맞아서 너를 위해 선물을 준비했어
나는 내일부터 3일 동안 부산에 가서 공연해
앞으로 미안해할 짓을 하면 안 될 거 같아
진짜 모차렐라 치즈를 듬뿍 넣어서 만든 느낌이야
다행히, 그의 고양이 하이디와 한스가 거기에 있었어
일단 영화의 색감이 너무 예뻐서 좋아해
당신은 욕심이 너무 지나쳐
이번 신호에서 우회전하면 되는 거지
그리고 혹시 두바이 전시회 후에 우리가 소개했던 신제품 자료를 a에게 전달했니
너 입사한 지 2년은 된 것 같은데 그동안 커튼을 한 번도 빨지 않았단 말이야
네가 보내 준 고귀한 이야기 정말 고마워
내가 알고 있는 여러 나라의 여자 중에 당신이 제일 귀여워
다들 맡은 일은 잘 해내고 있어서 다행인 것 같아
내 동생도 이렇게 미술품 전시회 하고 싶다고 난리야
나는 고객에게 거래 번호를 

오늘 7교시 끝나고 직업 특강이 있어
공연장 속으로 들어와 있는 것만 같아
너는 예전에 외국으로 출장을 가본 적이 있어
너는 졸업하고 이곳으로 이사 올 거니
어느 인보이스와 어떤 품목에 장착되어 선적되었는지 말해줘
너 아침에 차장님 간부회의에서 깨진 거 몰라
인도의 커리는 우리가 알고 있는 카레라이스와는 달라
좋은 생각이네, 마침 햄버거를 먹고 싶었어
상승 욕구가 강한 당신은 그만큼의 강한 재물 운도 같이 불러들이기 때문이야
한국은 팝 음악의 수입국이었어
우리가 또 언제 만날수 있을 지 모르잖아
난 소년의 눈빛이 굉장히 마음에 들고, 머즐과 큰 귀를 확인할 수 있었어
평소에 쇼핑을 많이 하진 않지만, 굉장히 좋아하는 편이어서 그런지 이곳을 꼭 가보고 싶어
저소득 장애인 근로자의 안정적 직업생활을 위한 지원책 마련
너를 항상 걱정하고 사랑하는 나의 마음을 알아줬으면 좋겠어
당신에게 외출 시, 여행 시에 가볍게 들고 갈 케이스가 필요했다면 라운드 케이스는 최고의 선택일 거야
이 주변에 식당들은 다 어디에 갔지
난 영어 번역기를 사용하지 않으면 힘들어
그래, 나도 화장품 사야 해서 마침 위층으로 가려고 했어
다들 바쁜데 이렇게 열심히 그룹 과제 참여해주는데, 이 정도는 뭐 괜찮아
가난하다고 자신을 절대 포기하지 마
당신은 이것에 대한 어떠한 말도 나에게 해주지 않았어
나는 네가 나를 좋아하는 걸 이용하고 싶진 않아
스마트폰은 우리 생활에 아주 밀접해 있어
웨이터를 불러서 물어보고 허락받고 찍어야 할 거 같아
그래서 오늘 아침에 친구와 운동을 하러 갔어
그래서 나는 길에서 만난 할머니를 집에 모셔다드렸어
2학년 때 수학여행을 갔던 것이 가장 기억에 남아, 정말 유익했는데
우리는 그 일을 하면서 정말 신나는 시간을 보냈지
우리가 입사한 게 엊그제 같은데 벌써 4년이나 되었네
당신이 거기에 있는 것조차 나에게는 힘이 돼
그 애는 새벽 3시까지 공부하던데, 나는 아침에 공부하는 성격이라서
내 주름살 좀 한 번 봐봐
난 토요일 저녁에 누굴 소개받기로 했어
내가 처음 주문한 

뒤에 응급차 소리도 들리는 거 보니 사고 맞는구나
치즈 종류가 정말 많은데 어떤 치즈를 골라야 하지
내가 좋아하는 친구를 소개해줄게
내가 오리건주에 있는 내 친구 브리더에게 물어보았어
생각 외로 숙소가 너무 좋은 것 같아. 풀빌라는 처음이라서 그런지
그 장면도 이번 공연에서 인상 깊게 본 장면 중 하나야
거스름돈을 줄 때 던지듯이 내어줘
나는 겨울 캠프를 하러 학교에 갔어
니가 원하는 대로 다음에 주문할 때 1개를 추가로 보내줄게
나는 그날 일 안 하는 날이야
사진으로는 절대 못 담는 현장만의 매력이 있다는 자신감이겠지
그럼 신발에 에어가 다 터져버리겠지
그래서 우리는 다음에 다시 만나는 게 좋을 거 같아
우리 부모님이 이혼한다고 절차 밟고 있어
치즈빵에 닭갈비 올려서 한 입에 먹어봐
그럼, 내년에 내가 필리핀 가면 너 없는 거야
다시 말해서, 야간요금을 산정하는 시간 기준으로 시간 5가 반영되도록 설정해줘
모두들 좋은 하루 보내길 바라
보호구역 안의 주민 또는 이해관계자 등의 지원에 관한 사항
나도 혼자 있을 때 내가 왜 이러는지 모르겠어
아까 나온 사람이 아이언맨이야
나도 그런데, 나 같은 사람이 또 있을 줄이야
기분이 좋아지려면 어떻게 해야 하지
새벽에 운행하는 공항버스는 시간이 좀 덜 걸리지 않나
너 같은 스타일 안 좋아하는 걸 모두가 알아
너는 걱정할 것 하나도 없어, 그냥 시키는 대로 하면 돼
너는 한국에서 좋은 남자 만나면 결혼할 수 있니
마네킹 생산이 완료되면 남은 금액에 대한 인보이스를 보내줘
케이팝이 가수의 비주얼적인 면에서 우월하긴 하지
우리 세 명이 다 같이 모이면 술 마시고 놀자
당신이 사는 나라의 최신소식을 공유해라
노마크는 돌아가신 부모님을 많이 생각할 정도로 착한 심성을 가지고 있으며 야구에 큰 재능이 있었어
전 여자친구랑 사귈 때도 결혼하고 싶다는 생각이 들었어
목적 이미지가 널 자극하고 있는 거야
내가 정오까지 거기로 갈 테니까 기다려
내가 정말 좋아하는 친구들을 만났거든
게시물에 RSB를 조립 난간 부분을 놓고 두 개의 A와 